<a href="https://colab.research.google.com/github/lilasch/Facial_Attribute_Classification/blob/main/liladatapreprocessing.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Facial Attribute Classification**

Lila Schisgal and Phoebe Jeske


First, we import our data from two text files and partition it into training and validation data.

In [ ]:
import zipfile
zippath = 'img_align_celeba.zip'
targetfolder = 'images'

with zipfile.ZipFile(zippath, 'r') as zip_ref:
    zip_ref.extractall(targetfolder)

In [13]:
from tensorflow import keras
import pandas as pd
import numpy as np
import glob
import shutil
import os


# from google.colab import drive
# drive.mount('/content/drive', force_remount = True)

# 40 attributes in total
num_attributes = 40

# Load attributes csv
# attributes = pd.read_csv("/content/drive/MyDrive/list_attr_celeba.txt", skiprows = 1, delimiter="\s+|\t")
attributes = pd.read_csv("list_attr_celeba.txt", skiprows = 1, delimiter="\s+|\t")

# Load csv with partitions values
# partitions = pd.read_csv("/content/drive/MyDrive/list_eval_partition.txt", delimiter="\s+|\t", header = None)
partitions = pd.read_csv("list_eval_partition.txt", delimiter="\s+|\t", header = None)


partitions.columns = ['image_name', 'dataset'] # setting column header names for partitions
attributes['dataset'] = partitions['dataset'].values # copying the partition values into the attributes df

# filter so just the eyeglasses attribute is included
glasses_df = attributes.iloc[:, [15, num_attributes]]

# partitioning the data
train_df = glasses_df[glasses_df['dataset'] == 0]
valid_df = glasses_df[glasses_df['dataset'] == 1]


y_train = train_df['Eyeglasses']
y_valid = valid_df['Eyeglasses']
del train_df['Eyeglasses']
del valid_df['Eyeglasses']

# getting our image file names in two arrays
train_files = train_df.index
valid_files = valid_df.index


image_folder = "images/img_align_celeba/"
valid_destination = "valid_images"
train_destination = "train_images"

# Function to split images based on classification
def split_images(source_folder):
    files = os.listdir(source_folder)  # Get the list of files in the source_folder
    for file in files:
        print(file)
        if file in train_files:
            shutil.move(os.path.join(source_folder, file), os.path.join(train_destination, file))
        elif file in valid_files:
            shutil.move(os.path.join(source_folder, file), os.path.join(valid_destination, file))
        else:
            continue

split_images(image_folder)


/var/folders/zz/p0bxtrc57nx_bmrp_9vns_r40000gn/T/ipykernel_96907/3495984511.py:24: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  attributes = pd.read_csv("list_attr_celeba.txt", skiprows = 1, delimiter="\s+|\t")
/var/folders/zz/p0bxtrc57nx_bmrp_9vns_r40000gn/T/ipykernel_96907/3495984511.py:28: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  partitions = pd.read_csv("list_eval_partition.txt", delimiter="\s+|\t", header = None)


052628.jpg
110369.jpg
161590.jpg
065084.jpg
108526.jpg
045354.jpg
139923.jpg
091663.jpg
107615.jpg
003301.jpg
195377.jpg
150995.jpg
141640.jpg
118735.jpg
126803.jpg
192418.jpg
075297.jpg
171783.jpg
160856.jpg
151453.jpg
185164.jpg
013112.jpg
117406.jpg
081470.jpg
055147.jpg
043725.jpg
101264.jpg
097212.jpg
074189.jpg
193706.jpg
005770.jpg
147231.jpg
054259.jpg
148102.jpg
116718.jpg
141898.jpg
098121.jpg
109638.jpg
157022.jpg
015563.jpg
183515.jpg
087001.jpg
111077.jpg
053536.jpg
062933.jpg
088332.jpg
194069.jpg
158311.jpg
024966.jpg
047543.jpg
019359.jpg
093074.jpg
105002.jpg
001516.jpg
197560.jpg
143057.jpg
198653.jpg
189986.jpg
030913.jpg
163387.jpg
084508.jpg
067693.jpg
048670.jpg
039089.jpg
076946.jpg
153244.jpg
187773.jpg
011705.jpg
115211.jpg
046885.jpg
083267.jpg
069866.jpg
057750.jpg
144738.jpg
006279.jpg
077480.jpg
058463.jpg
173194.jpg
188440.jpg
008254.jpg
174823.jpg
082179.jpg
132876.jpg
041132.jpg
103473.jpg
095405.jpg
028184.jpg
191111.jpg
007167.jpg
145426.jpg
142349.jpg

KeyboardInterrupt: 

We then separate our target y values and image filenames in preparation for accessing the actual images as vectors.

Next: need to access the images from the dataset and put them into a set of vectors.

In [14]:
from PIL import Image
from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt

# Set your folder paths
valid_folder = "valid_images/"
train_folder = "train_images/"

# Function to normalize images
def normalize_images(image_path):
    save_array = []
    for filename in os.listdir(image_path):
        if filename.endswith(".jpg"):
            img_path = os.path.join(image_path, filename)
            print(img_path)
            img = Image.open(img_path)
            img_array = np.array(img)
            flattened_dim = 218 * 178 * 3
            img_processed = img_array.reshape(-1, flattened_dim)
            img_processed = img_processed.astype(float)
            save_array.append(img_processed)
    return save_array

def standardize(train, valid):
    mean = np.mean(train)
    std = np.std(train)

    train = (train - mean)/std
    valid = (valid - mean)/std

    return train, valid

# Apply preprocessing steps
valid_images = normalize_images(valid_folder)
train_images = normalize_images(train_folder)
standardized_train, stardized_valid = standardize(valid_images, train_images)


valid_images/171783.jpg
(218, 178, 3)
valid_images/163387.jpg
(218, 178, 3)
valid_images/173194.jpg
(218, 178, 3)
valid_images/174823.jpg
(218, 178, 3)
valid_images/181302.jpg
(218, 178, 3)
valid_images/175283.jpg
(218, 178, 3)
valid_images/181464.jpg
(218, 178, 3)
valid_images/165090.jpg
(218, 178, 3)
valid_images/162927.jpg
(218, 178, 3)
valid_images/169872.jpg
(218, 178, 3)
valid_images/177494.jpg
(218, 178, 3)
valid_images/167687.jpg
(218, 178, 3)
valid_images/176952.jpg
(218, 178, 3)
valid_images/166599.jpg
(218, 178, 3)
valid_images/169866.jpg
(218, 178, 3)
valid_images/177480.jpg
(218, 178, 3)
valid_images/176946.jpg
(218, 178, 3)
valid_images/167693.jpg
(218, 178, 3)
valid_images/182179.jpg
(218, 178, 3)
valid_images/175297.jpg
(218, 178, 3)
valid_images/181470.jpg
(218, 178, 3)
valid_images/165084.jpg
(218, 178, 3)
valid_images/162933.jpg
(218, 178, 3)
valid_images/174189.jpg
(218, 178, 3)
valid_images/180008.jpg
(218, 178, 3)
valid_images/163393.jpg
(218, 178, 3)
valid_images

: 